In [1]:
# this assumes that you have a proper version of PyTorch already installed
!pip install -q torchaudio omegaconf soundfile
# You may need this:
# !pip install librosa==0.8.0
# The librosa versions are super weird and incompatible with various other dependencies.
# You might have to google bugs on SO and install a different version number. 0.8.0 is pretty old.

# MAKE SURE YOU HAVE FFMPEG INSTALLED
# FFMPEG will come from os pkg manager, not pip. Try brew or apt.

You should consider upgrading via the '/home/carden.bagwell/Envs/jupyter3/bin/python3 -m pip install --upgrade pip' command.


In [2]:
!pip install youtube-dl

You should consider upgrading via the '/home/carden.bagwell/Envs/jupyter3/bin/python3 -m pip install --upgrade pip' command.


In [114]:
import os
# download youtube url using ffmpeg
# adapted from: https://github.com/ytdl-org/youtube-dl/issues/622#issuecomment-162337869
def download_from_url_ffmpeg(url, output, start_seconds=0, duration_seconds = 60):

  output = os.path.abspath(output)
  try:
    os.remove(output)
  except:
    print(f"Couldn't remove {output}")
    pass
  print(os.path.abspath(output))
  cmd = f'ffmpeg -loglevel warning -ss {start_seconds} -i $(youtube-dl -f bestaudio --get-url {url}) -t {duration_seconds} -ac 1 -ar 22050 {output}'
  # Print the cmd for debugging. Check the notebook server log if it isn't working.
  print(cmd)
  os.system(cmd)

  return output

In [115]:
# 10 minute rant url
url = 'https://www.youtube.com/watch?v=TFl2u0HavS0'
audio_files = []
start_duration_tuples = [
    (30, 21),
    (51, 21),
    #1:18-1:37
    (78, 19),
    #1:43-1:51 - can go to 1:58 but has TTS interrupt
    (103, 8),
    #2:18-3:18
    (138, 51),
    (193, 7),
    #5:02-5:17
    (302, 15),
    #5:22-5:38
    (322, 16),
    #6:45-6:54
    (405, 9),
    #6:57-7:08
    (417, 11),
    #8:25-8:41
    (505, 16),
    #8:43-9:06
    (523, 23),
    #9:36-9:44
    (576, 8),
    #9:47-9:53
    (587, 6),
    
]
for i, (start, duration) in enumerate(start_duration_tuples):
    # Had a bug where I thought the dataset only allowed 8s clips.
    # I don't think this is actually the case, but you can limit the length here.
    # duration = min(duration, 8)
    
    # Make sure you create the `./artosis/` directory first.
    # download_from_url_ffmpeg will create the file but not mkdir.
    fname = f'artosis/artosis_rant_{i}.wav'
    audio_files.append(download_from_url_ffmpeg(url, fname, start_seconds=start, duration_seconds=duration))

/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_0.wav
ffmpeg -loglevel warning -ss 30 -i $(youtube-dl -f bestaudio --get-url https://www.youtube.com/watch?v=TFl2u0HavS0) -t 8 -ac 1 -ar 22050 /home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_0.wav
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_1.wav
ffmpeg -loglevel warning -ss 51 -i $(youtube-dl -f bestaudio --get-url https://www.youtube.com/watch?v=TFl2u0HavS0) -t 8 -ac 1 -ar 22050 /home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_1.wav
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_2.wav
ffmpeg -loglevel warning -ss 78 -i $(youtube-dl -f bestaudio --get-url https://www.youtube.com/watch?v=TFl2u0HavS0) -t 8 -ac 1 -ar 22050 /home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_2.wav
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_3.wav
ffmpeg -loglevel warning -ss 

In [116]:
from IPython.display import Audio

In [117]:
# You need a cell for each one of these, so I hard coded the indices.
Audio(filename=audio_files[0])


In [118]:
Audio(filename=audio_files[1])

In [119]:
Audio(filename=audio_files[2])

In [120]:
Audio(filename=audio_files[3])

In [121]:
Audio(filename=audio_files[4])

In [122]:
Audio(filename=audio_files[5])

In [123]:
Audio(filename=audio_files[6])

In [124]:
Audio(filename=audio_files[7])

In [125]:
Audio(filename=audio_files[8])

In [126]:
Audio(filename=audio_files[9])

In [127]:
Audio(filename=audio_files[10])

In [128]:
Audio(filename=audio_files[11])

In [129]:
Audio(filename=audio_files[12])

In [130]:
Audio(filename=audio_files[13])

In [131]:
# THIS IS WHERE THE SPEECH TO TEXT OCCURS
# We download the model from torch hub
# I had to chmod 777 ~/.cache/torch for torch hub to work for my notebook in a virtualenv.

# This is pretty fast.

import torch
import zipfile
import torchaudio
from glob import glob

device = torch.device('cpu')  # gpu also works, but our models are fast enough for CPU

model, decoder, utils = torch.hub.load(repo_or_dir='snakers4/silero-models',
                                       model='silero_stt',
                                       language='en', # also available 'de', 'es'
                                       device=device)
(read_batch, split_into_batches,
 read_audio, prepare_model_input) = utils  # see function signature for details

# This is from the 
# download a single file, any format compatible with TorchAudio (soundfile backend)
# torch.hub.download_url_to_file('https://opus-codec.org/static/examples/samples/speech_orig.wav',
#                                dst ='speech_orig.wav', progress=True)
# test_files = glob('speech_orig.wav')
test_files = audio_files
batches = split_into_batches(test_files, batch_size=1)
for b, fpath in zip(batches, test_files):
    input = prepare_model_input(read_batch(b),
                            device=device)

    output = model(input)
    for example in output:
        # Format the output in the format of a flowtron filelist for fine tuning.
        print(f'{fpath}|{decoder(example.cpu())}|0')

Using cache found in /home/carden.bagwell/.cache/torch/hub/snakers4_silero-models_master


/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_0.wav|these pieces of shit these absolute pieces of shit|0
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_1.wav|just keeps drawn his probe and like the zone pops out a half second for the gate d and then when i'm tryingto do the bunker rush|0
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_2.wav|this is so fucked up it's so fucked up i have lost fifty points to stream|0
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_3.wav|you see me play against bufucking proses are twentyththree twenty mar bucking mr greata games great games|0
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_4.wav|i hate this i can't even fuc and explain you how much i hate this i can't even|0
/home/carden.bagwell/gitrepos/spiyer99.github.io/nbs/artosis/artosis_rant_5.wav|every daypeople are trying to ruin me|0
/home/carden.bagwell/gitrepos/s

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import inference

In [30]:
import json
import os
import torch

# python inference.py -c config.json -f outdir/model_89000 -w models/waveglow_256channels_universal_v5.pt -t "It is well know that deep generative models have a rich latent space!" -i 0
config_path = './config.json'
params = []
flowtron_path = './outdir/model_40000'
waveglow_path = './models/waveglow_256channels_universal_v5.pt'
text =  "this is so fucked up it's so fucked up" 
text =  "Hey ricardo this is artosis. Just wanted to let you know that terran is retarded"
output_dir = './outdir/'
# Maybe I need to change this? 
id = 0
n_frames = 400
sigma = 0.5
gate = 0.5
seed = 1234

# Parse configs.  Globals nicer in this case
with open(config_path) as f:
    data = f.read()

global config
config = json.loads(data)
inference.update_params(config, params)

data_config = config["data_config"]
global model_config
model_config = config["model_config"]

# Make directory if it doesn't exist
if not os.path.isdir(output_dir):
    os.makedirs(output_dir)
    os.chmod(output_dir, 0o775)

torch.backends.cudnn.enabled = True
torch.backends.cudnn.benchmark = False
inference.infer(flowtron_path, waveglow_path, output_dir, text,
      id, n_frames, sigma, gate, seed, model_config, data_config)

Loaded checkpoint './outdir/model_40000')
Number of speakers : 1
Number of speakers : 1
(102400,)


In [31]:
from IPython.display import Audio

In [32]:
Audio(filename='./outdir/sid0_sigma0.5.wav')